In [3]:
!pip install opencv-python-headless matplotlib pandas keras numpy scikit-image scikit-learn tqdm


  Using cached opencv_python_headless-4.9.0.80-cp37-abi3-win_amd64.whl (38.5 MB)


You should consider upgrading via the 'C:\Users\Bruce\AppData\Local\Programs\Python\Python310\python.exe -m pip install --upgrade pip' command.


In [2]:
!pip install tqdm

  Using cached tqdm-4.66.4-py3-none-any.whl (78 kB)


You should consider upgrading via the 'C:\Users\Bruce\AppData\Local\Programs\Python\Python310\python.exe -m pip install --upgrade pip' command.


In [2]:
import cv2 # for capturing videos

import math # for mathematical operations

import matplotlib.pyplot as plt # for plotting the images

%matplotlib inline

import pandas as pd

from keras.preprocessing import image # for preprocessing the images

import numpy as np # for mathematical operations

#from keras.utils import np_utils
#from keras.utils.np_utils import to_categorical
from keras.utils import to_categorical

from skimage.transform import resize # for resizing images

from sklearn.model_selection import train_test_split

from glob import glob

from tqdm import tqdm

In [5]:
pip show sklearn


Name: sklearn
Version: 0.0
Summary: A set of python modules for machine learning and data mining
Home-page: https://pypi.python.org/pypi/scikit-learn/
Author: UNKNOWN
Author-email: UNKNOWN
License: 
Location: c:\users\bruce\appdata\local\programs\python\python310\lib\site-packages
Requires: scikit-learn
Required-by: 
Note: you may need to restart the kernel to use updated packages.


In [4]:
import os

# Path to the video folder
video_folder = 'E:\\Projects\\AI\\videoclassificationmodel\\Videos\\UCF-101'


# Get the list of video file names in the folder
video_files = os.listdir(video_folder)

# Create a .txt file and write the video names to it
with open('video_names.txt', 'w') as f:
    for video_file in video_files:
        f.write(f"{video_file}\n")

# Read the created .txt file into a DataFrame using pandas
video_names_df = pd.read_csv('video_names.txt', header=None, names=['video_name'])

# Display the first few rows of the DataFrame
print(video_names_df.head())


       video_name
0  ApplyEyeMakeup
1   ApplyLipstick
2         Archery
3    BabyCrawling
4     BalanceBeam


In [11]:
import pandas as pd

# open the .txt file which have names of training videos

f = open("trainlist01.txt", "r")

temp = f.read()

videos = temp.split('\n')

# creating a dataframe having video names

train = pd.DataFrame()

train['video_name'] = videos

train = train[:-1]

#print(train.head())
train.head()

video_name
0  ApplyEyeMakeup
1   ApplyLipstick
2         Archery
3    BabyCrawling
4     BalanceBeam

In [62]:
# open the .txt file which have names of test videos

f = open("testlist01.txt", "r")

temp = f.read()

videos = temp.split('\n') 

# creating a dataframe having video names

test = pd.DataFrame()

test['video_name'] = videos

test = test[:-1]

test.head()

video_name
0  ApplyEyeMakeup
1   ApplyLipstick
2         Archery
3    BabyCrawling
4     BalanceBeam

In [14]:
train.shape[0]

101

In [18]:
# creating tags for training videos

train_video_tag = []

for i in range(train.shape[0]):   

      train_video_tag.append(train['video_name'][i].split('/')[0]) 

train['tag'] = train_video_tag 

# creating tags for test videos

test_video_tag = []

for i in range(test.shape[0]):   

     test_video_tag.append(test['video_name'][i].split('/')[0]) 

test['tag'] = test_video_tag


In [19]:
print(train['tag'])

0         ApplyEyeMakeup
1          ApplyLipstick
2                Archery
3           BabyCrawling
4            BalanceBeam
             ...        
96     VolleyballSpiking
97        WalkingWithDog
98           WallPushups
99        WritingOnBoard
100                 YoYo
Name: tag, Length: 101, dtype: object


In [51]:
print(test['tag'])

0         ApplyEyeMakeup
1          ApplyLipstick
2                Archery
3           BabyCrawling
4            BalanceBeam
             ...        
96     VolleyballSpiking
97        WalkingWithDog
98           WallPushups
99        WritingOnBoard
100                 YoYo
Name: tag, Length: 101, dtype: object


In [153]:
# storing the frames from training videos

# Output folder where images will be saved
output_folder = 'train_1'

# Create the output folder if it doesn't exist
os.makedirs(output_folder, exist_ok=True)
for i in tqdm(range(train.shape[0])):

       count = 0 

       videoFile = train['video_name'][i]
       
       #print('Videos/UCF-101/'+videoFile.split(' ')[0].split('/')[0])
    
    
       folder_path = 'Videos/UCF-101/'+videoFile.split(' ')[0].split('/')[0]
       # Get the list of video files in the folder
       video_files = [f for f in os.listdir(folder_path) if f.endswith('.avi')]
       for video_file in video_files:
            video_path = os.path.join(folder_path, video_file)  # Full path to the video file
        
            # Capture the video from the given path
            cap = cv2.VideoCapture(video_path)
            #print(video_path)
            #cap = cv2.VideoCapture() # capturing the video from the given path 
            #print(cap)
        
            frameRate = cap.get(5) #frame rate 
        
            x=1
            while(cap.isOpened()):

               frameId = cap.get(1) #current frame number 
        
               ret, frame = cap.read() 
        
               if (ret != True): 
        
                   break 
               try :
        
                   if (frameId % math.floor(frameRate) == 0):
            
                     # storing the frames in a new folder named train_1 
                    
                            ##filename ='train_1\\' + video_path +"_frame%d.jpg" % count;count+=1 
                            #print(filename)
                    
                            #cv2.imwrite(filename, frame) 
                             video_filename = os.path.basename(video_path)
        
                            # Remove the .avi extension from the video filename
                             video_filename = os.path.splitext(video_filename)[0]
                             #print(video_filename)
                            
                            # Construct the filename for the frame
                             filename = output_folder+'/' + video_filename + "_frame%d.jpg" % count;count+=1 
                             if not cv2.imwrite(filename, frame):
                                 raise Exception("Could not write image")
                             print(filename)
                            
                            # Increment the count for the next frame
                             #count += 1
               except Exception as e:
                print(f"Error: {e}")
                raise SystemExit("Error occurred. Stopping cell execution.")
            
            cap.release()
            

  0%|                                                                                          | 0/101 [00:00<?, ?it/s]

train_1/v_ApplyEyeMakeup_g01_c01_frame0.jpg
train_1/v_ApplyEyeMakeup_g01_c01_frame1.jpg
train_1/v_ApplyEyeMakeup_g01_c01_frame2.jpg
train_1/v_ApplyEyeMakeup_g01_c01_frame3.jpg
train_1/v_ApplyEyeMakeup_g01_c01_frame4.jpg
train_1/v_ApplyEyeMakeup_g01_c01_frame5.jpg
train_1/v_ApplyEyeMakeup_g01_c01_frame6.jpg
train_1/v_ApplyEyeMakeup_g01_c02_frame7.jpg
train_1/v_ApplyEyeMakeup_g01_c02_frame8.jpg
train_1/v_ApplyEyeMakeup_g01_c02_frame9.jpg
train_1/v_ApplyEyeMakeup_g01_c02_frame10.jpg
train_1/v_ApplyEyeMakeup_g01_c02_frame11.jpg
train_1/v_ApplyEyeMakeup_g01_c03_frame12.jpg
train_1/v_ApplyEyeMakeup_g01_c03_frame13.jpg
train_1/v_ApplyEyeMakeup_g01_c03_frame14.jpg
train_1/v_ApplyEyeMakeup_g01_c03_frame15.jpg
train_1/v_ApplyEyeMakeup_g01_c03_frame16.jpg
train_1/v_ApplyEyeMakeup_g01_c03_frame17.jpg
train_1/v_ApplyEyeMakeup_g01_c03_frame18.jpg
train_1/v_ApplyEyeMakeup_g01_c03_frame19.jpg
train_1/v_ApplyEyeMakeup_g01_c03_frame20.jpg
train_1/v_ApplyEyeMakeup_g01_c03_frame21.jpg
train_1/v_ApplyEyeMa

  1%|▊                                                                                 | 1/101 [00:11<18:56, 11.37s/it]

train_1/v_ApplyEyeMakeup_g25_c07_frame1038.jpg
train_1/v_ApplyEyeMakeup_g25_c07_frame1039.jpg
train_1/v_ApplyEyeMakeup_g25_c07_frame1040.jpg
train_1/v_ApplyEyeMakeup_g25_c07_frame1041.jpg
train_1/v_ApplyEyeMakeup_g25_c07_frame1042.jpg
train_1/v_ApplyLipstick_g01_c01_frame0.jpg
train_1/v_ApplyLipstick_g01_c01_frame1.jpg
train_1/v_ApplyLipstick_g01_c01_frame2.jpg
train_1/v_ApplyLipstick_g01_c01_frame3.jpg
train_1/v_ApplyLipstick_g01_c01_frame4.jpg
train_1/v_ApplyLipstick_g01_c01_frame5.jpg
train_1/v_ApplyLipstick_g01_c02_frame6.jpg
train_1/v_ApplyLipstick_g01_c02_frame7.jpg
train_1/v_ApplyLipstick_g01_c02_frame8.jpg
train_1/v_ApplyLipstick_g01_c02_frame9.jpg
train_1/v_ApplyLipstick_g01_c02_frame10.jpg
train_1/v_ApplyLipstick_g01_c02_frame11.jpg
train_1/v_ApplyLipstick_g01_c02_frame12.jpg
train_1/v_ApplyLipstick_g01_c03_frame13.jpg
train_1/v_ApplyLipstick_g01_c03_frame14.jpg
train_1/v_ApplyLipstick_g01_c03_frame15.jpg
train_1/v_ApplyLipstick_g01_c03_frame16.jpg
train_1/v_ApplyLipstick_g01

  2%|█▌                                                                                | 2/101 [00:22<18:21, 11.13s/it]

...

 99%|███████████████████████████████████████████████████████████████████████████████▏| 100/101 [17:58<00:09,  9.81s/it]

train_1/v_WritingOnBoard_g25_c07_frame1046.jpg
train_1/v_WritingOnBoard_g25_c07_frame1047.jpg
train_1/v_YoYo_g01_c01_frame0.jpg
train_1/v_YoYo_g01_c01_frame1.jpg
train_1/v_YoYo_g01_c01_frame2.jpg
train_1/v_YoYo_g01_c01_frame3.jpg
train_1/v_YoYo_g01_c01_frame4.jpg
train_1/v_YoYo_g01_c01_frame5.jpg
train_1/v_YoYo_g01_c01_frame6.jpg
train_1/v_YoYo_g01_c01_frame7.jpg
train_1/v_YoYo_g01_c02_frame8.jpg
train_1/v_YoYo_g01_c02_frame9.jpg
train_1/v_YoYo_g01_c02_frame10.jpg
train_1/v_YoYo_g01_c02_frame11.jpg
train_1/v_YoYo_g01_c02_frame12.jpg
train_1/v_YoYo_g01_c02_frame13.jpg
train_1/v_YoYo_g01_c02_frame14.jpg
train_1/v_YoYo_g01_c02_frame15.jpg
train_1/v_YoYo_g01_c03_frame16.jpg
train_1/v_YoYo_g01_c03_frame17.jpg
train_1/v_YoYo_g01_c03_frame18.jpg
train_1/v_YoYo_g01_c03_frame19.jpg
train_1/v_YoYo_g01_c03_frame20.jpg
train_1/v_YoYo_g01_c03_frame21.jpg
train_1/v_YoYo_g01_c03_frame22.jpg
train_1/v_YoYo_g01_c04_frame23.jpg
train_1/v_YoYo_g01_c04_frame24.jpg
train_1/v_YoYo_g01_c04_frame25.jpg
train_

100%|████████████████████████████████████████████████████████████████████████████████| 101/101 [18:08<00:00,  9.85s/it]

train_1/v_YoYo_g25_c03_frame976.jpg
train_1/v_YoYo_g25_c03_frame977.jpg
train_1/v_YoYo_g25_c03_frame978.jpg
train_1/v_YoYo_g25_c03_frame979.jpg
train_1/v_YoYo_g25_c04_frame980.jpg
train_1/v_YoYo_g25_c04_frame981.jpg
train_1/v_YoYo_g25_c04_frame982.jpg
train_1/v_YoYo_g25_c04_frame983.jpg
train_1/v_YoYo_g25_c04_frame984.jpg
train_1/v_YoYo_g25_c04_frame985.jpg
train_1/v_YoYo_g25_c04_frame986.jpg
train_1/v_YoYo_g25_c04_frame987.jpg
train_1/v_YoYo_g25_c05_frame988.jpg
train_1/v_YoYo_g25_c05_frame989.jpg
train_1/v_YoYo_g25_c05_frame990.jpg
train_1/v_YoYo_g25_c05_frame991.jpg
train_1/v_YoYo_g25_c05_frame992.jpg
train_1/v_YoYo_g25_c05_frame993.jpg
train_1/v_YoYo_g25_c05_frame994.jpg
train_1/v_YoYo_g25_c05_frame995.jpg


100%|████████████████████████████████████████████████████████████████████████████████| 101/101 [18:08<00:00, 10.77s/it]


In [164]:
# getting the names of all the images

images = glob("train_1/*.jpg")

train_image = []

train_class = []

for i in tqdm(range(len(images))): 

       # creating the image name  

       #train_image.append(images[i].split('/')[0]) 

      # creating the class of image   

       #train_class.append(images[i].split('/')[0].split('_')[1])
       # Split the image path by the directory separator '/'
        image_parts = images[i].split('\\')
        # Get the last part of the path, which is the filename
        image_name = image_parts[-1]
        # Split the filename by '_' to extract the class
        image_class = image_name.split('_')[1]
        print(image_name)
        print(image_class)
        # Append the image name and class to their respective lists
        train_image.append(image_name)
        train_class.append(image_class) 

# storing the images and their class in a dataframe

train_data = pd.DataFrame()

train_data['image'] = train_image

train_data['class'] = train_class 

# converting the dataframe into csv file 

train_data.to_csv('train_new.csv',header=True, index=False)

  9%|██████▉                                                                  | 9719/102741 [00:00<00:01, 91419.15it/s]

v_ApplyEyeMakeup_g01_c01_frame0.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c01_frame1.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c01_frame2.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c01_frame3.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c01_frame4.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c01_frame5.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c01_frame6.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c02_frame10.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c02_frame11.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c02_frame7.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c02_frame8.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c02_frame9.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c03_frame12.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c03_frame13.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c03_frame14.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c03_frame15.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c03_frame16.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c03_frame17.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c03_frame18.jpg
ApplyEyeMakeup
v_ApplyEyeMakeup_g01_c

 30%|█████████████████████▉                                                  | 31336/102741 [00:00<00:00, 89654.31it/s]

v_CricketBowling_g19_c06_frame467.jpg
CricketBowling
v_CricketBowling_g19_c07_frame468.jpg
CricketBowling
v_CricketBowling_g19_c07_frame469.jpg
CricketBowling
v_CricketBowling_g19_c07_frame470.jpg
CricketBowling
v_CricketBowling_g19_c07_frame471.jpg
CricketBowling
v_CricketBowling_g20_c01_frame472.jpg
CricketBowling
v_CricketBowling_g20_c01_frame473.jpg
CricketBowling
v_CricketBowling_g20_c01_frame474.jpg
CricketBowling
v_CricketBowling_g20_c01_frame475.jpg
CricketBowling
v_CricketBowling_g20_c01_frame476.jpg
CricketBowling
v_CricketBowling_g20_c01_frame477.jpg
CricketBowling
v_CricketBowling_g20_c02_frame478.jpg
CricketBowling
v_CricketBowling_g20_c02_frame479.jpg
CricketBowling
v_CricketBowling_g20_c02_frame480.jpg
CricketBowling
v_CricketBowling_g20_c02_frame481.jpg
CricketBowling
v_CricketBowling_g20_c02_frame482.jpg
CricketBowling
v_CricketBowling_g20_c03_frame483.jpg
CricketBowling
v_CricketBowling_g20_c03_frame484.jpg
CricketBowling
v_CricketBowling_g20_c03_frame485.jpg
CricketB

 50%|████████████████████████████████████                                    | 51389/102741 [00:00<00:00, 89006.70it/s]


IceDancing
v_IceDancing_g17_c03_frame1062.jpg
IceDancing
v_IceDancing_g17_c03_frame1063.jpg
IceDancing
v_IceDancing_g17_c03_frame1064.jpg
IceDancing
v_IceDancing_g17_c04_frame1065.jpg
IceDancing
v_IceDancing_g17_c04_frame1066.jpg
IceDancing
v_IceDancing_g17_c04_frame1067.jpg
IceDancing
v_IceDancing_g17_c04_frame1068.jpg
IceDancing
v_IceDancing_g17_c04_frame1069.jpg
IceDancing
v_IceDancing_g17_c04_frame1070.jpg
IceDancing
v_IceDancing_g17_c04_frame1071.jpg
IceDancing
v_IceDancing_g17_c04_frame1072.jpg
IceDancing
v_IceDancing_g17_c04_frame1073.jpg
IceDancing
v_IceDancing_g17_c04_frame1074.jpg
IceDancing
v_IceDancing_g17_c05_frame1075.jpg
IceDancing
v_IceDancing_g17_c05_frame1076.jpg
IceDancing
v_IceDancing_g17_c05_frame1077.jpg
IceDancing
v_IceDancing_g17_c05_frame1078.jpg
IceDancing
v_IceDancing_g17_c05_frame1079.jpg
IceDancing
v_IceDancing_g17_c05_frame1080.jpg
IceDancing
v_IceDancing_g17_c05_frame1081.jpg
IceDancing
v_IceDancing_g17_c05_frame1082.jpg
IceDancing
v_IceDancing_g17_c05_f

 67%|████████████████████████████████████████████████▎                       | 68926/102741 [00:00<00:00, 70321.89it/s]IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [3]:
import keras

from keras.models import Sequential

from keras.applications.vgg16 import VGG16

from keras.layers import Dense, InputLayer, Dropout, Flatten

from keras.layers import Conv2D, MaxPooling2D, GlobalMaxPooling2D

from keras.preprocessing import image

import numpy as np

import pandas as pd

import matplotlib.pyplot as plt

from tqdm import tqdm

from sklearn.model_selection import train_test_split

In [4]:
train = pd.read_csv('train_new.csv')

train.head()

image           class
0  v_ApplyEyeMakeup_g01_c01_frame0.jpg  ApplyEyeMakeup
1  v_ApplyEyeMakeup_g01_c01_frame1.jpg  ApplyEyeMakeup
2  v_ApplyEyeMakeup_g01_c01_frame2.jpg  ApplyEyeMakeup
3  v_ApplyEyeMakeup_g01_c01_frame3.jpg  ApplyEyeMakeup
4  v_ApplyEyeMakeup_g01_c01_frame4.jpg  ApplyEyeMakeup

In [ ]:
# creating an empty list

train_image = [] 

# for loop to read and store frames

for i in tqdm(range(train.shape[0])): 

      # loading the image and keeping the target size as (224,224,3) 

      img = image.load_img('train_1/'+train['image'][i], target_size=(224,224,3))

     # converting it to array

      img = image.img_to_array(img)

     # normalizing the pixel value 

      img = img/255

    # appending the image to the train_image list    

      train_image.append(img) 

# converting the list to numpy array

X = np.array(train_image) 

# shape of the array

X.shape

 56%|█████████████████████████████████████████▊                                 | 57332/102741 [15:39<39:35, 19.12it/s]

In [5]:
import numpy as np
from tensorflow.keras.preprocessing import image

# Assuming train_data is your DataFrame with image paths

# Define batch size
batch_size = 2

# Create an empty list to store batches of images
batch_images = []

# Iterate over the image paths in batches
#for i in range(0, len(train_data), batch_size):
for i in tqdm(range(0, train.shape[0], batch_size) ):
    # Get a batch of image paths
    batch_paths = train['image'].iloc[i:i+batch_size].tolist()
    
    # Load and preprocess each image in the batch
    batch_imgs = []
    for path in batch_paths:
        img = image.load_img('train_1/' + path, target_size=(64, 64))
        img = image.img_to_array(img)
        img = img/255  # Normalizing pixel values
        batch_imgs.append(img)
    
    # Append the batch of images to the list
    batch_images.append(np.array(batch_imgs))

# Convert the list of batches into a numpy array
X_batched = np.concatenate(batch_images, axis=0)

# Check the shape of the batched array
print("Shape of batched images array:", X_batched.shape)


100%|████████████████████████████████████████████████████████████████████████████| 51371/51371 [12:09<00:00, 70.43it/s]


Shape of batched images array: (102741, 64, 64, 3)


In [28]:
# separating the target

y = train['class'] 

# creating the training and validation set

X_train, X_test, y_train, y_test = train_test_split(X_batched, y, random_state=42, test_size=0.2, stratify = y)

In [29]:
# creating dummies of target variable for train and validation set

y_train = pd.get_dummies(y_train)
y_test = pd.get_dummies(y_test)

In [30]:
# creating the base model of pre-trained VGG16 model

base_model = VGG16(weights='imagenet', include_top=False)

In [31]:
# extracting features for training frames

X_train = base_model.predict(X_train)
X_train.shape

2569/2569 ━━━━━━━━━━━━━━━━━━━━ 2218s 863ms/step


(82192, 2, 2, 512)

In [32]:
# extracting features for validation frames

X_test = base_model.predict(X_test)
X_test.shape

643/643 ━━━━━━━━━━━━━━━━━━━━ 532s 827ms/step


(20549, 2, 2, 512)

In [33]:
# reshaping the training as well as validation frames in single dimension

X_train = X_train.reshape(82192, 2*2*512)
X_test = X_test.reshape(20549, 2*2*512)

In [34]:
# normalizing the pixel values

max = X_train.max()
X_train = X_train/max
X_test = X_test/max

In [35]:
# shape of images

X_train.shape

(82192, 2048)

In [36]:
#defining the classifier model architecture

model = Sequential()

model.add(Dense(1024, activation='relu', input_shape=(2048,)))

model.add(Dropout(0.5))

model.add(Dense(512, activation='relu'))

model.add(Dropout(0.5))

model.add(Dense(256, activation='relu'))

model.add(Dropout(0.5))

model.add(Dense(128, activation='relu'))

model.add(Dropout(0.5))

model.add(Dense(101, activation='softmax'))

C:\Users\Bruce\AppData\Local\Programs\Python\Python310\lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


In [50]:
# defining a function to save the weights of best model

from keras.callbacks import ModelCheckpoint

mcp_save = ModelCheckpoint('weight.keras', save_best_only=True, monitor='val_loss', mode='min')

In [51]:
# compiling the model

model.compile(loss='categorical_crossentropy',optimizer='Adam',metrics=['accuracy'])

In [52]:
# training the model
model.fit(X_train, y_train, epochs=200, validation_data=(X_test, y_test), callbacks=[mcp_save], batch_size=128)

Epoch 1/200
643/643 ━━━━━━━━━━━━━━━━━━━━ 47s 69ms/step - accuracy: 0.0642 - loss: 4.2317 - val_accuracy: 0.2781 - val_loss: 2.7774
Epoch 2/200
643/643 ━━━━━━━━━━━━━━━━━━━━ 44s 68ms/step - accuracy: 0.2531 - loss: 2.9288 - val_accuracy: 0.4622 - val_loss: 2.0762
Epoch 3/200
643/643 ━━━━━━━━━━━━━━━━━━━━ 44s 68ms/step - accuracy: 0.3734 - loss: 2.3733 - val_accuracy: 0.5567 - val_loss: 1.7006
Epoch 4/200
643/643 ━━━━━━━━━━━━━━━━━━━━ 82s 68ms/step - accuracy: 0.4470 - loss: 2.0644 - val_accuracy: 0.6035 - val_loss: 1.4622
Epoch 5/200
643/643 ━━━━━━━━━━━━━━━━━━━━ 44s 68ms/step - accuracy: 0.5064 - loss: 1.8272 - val_accuracy: 0.6638 - val_loss: 1.2737
Epoch 6/200
643/643 ━━━━━━━━━━━━━━━━━━━━ 46s 71ms/step - accuracy: 0.5409 - loss: 1.6846 - val_accuracy: 0.6898 - val_loss: 1.1740
Epoch 7/200
643/643 ━━━━━━━━━━━━━━━━━━━━ 46s 71ms/step - accuracy: 0.5715 - loss: 1.5685 - val_accuracy: 0.7070 - val_loss: 1.0751
Epoch 8/200
643/643 ━━━━━━━━━━━━━━━━━━━━ 45s 70ms/step - accuracy: 0.5998 - loss: 1

In [27]:
print(y.shape)
print(X_test.shape)
print(y_test.shape)

(102741,)
(20549, 2048)
(20549,)
